# bayes search parameter selection

In [1]:
# !python -m rpy2.situation

In [3]:
from pre_processing import remove_html_tags, preprocess_data, prepare_corpus
from post_processing import topic_selection
# from rpy2 import robjects #loading R inside Python
# #importing functions to read pandas DF
# from rpy2.robjects import pandas2ri
# pandas2ri.activate()
# from rpy2.robjects.packages import importr
# from rpy2.robjects.conversion import localconverter

import pandas as pd

import numpy as np

import os

#import R base library
# base = importr('base')

mallet_path = 'mallet' #'mallet for mac-os

In [4]:
stop_words = []

with open('freqPOS+Names.stop','r') as txtfile:
    for r in txtfile:
        stop_words.append(r.strip())
        if "'" in r:#add the term without "'"; e.g., haven't & havent
            stop_words.append(r.replace("'","").strip())

#adding the selected stop_words
stop_words.extend(['feel', 'get', 'good', 'life', 'really', 'time'])

stop_words[10:15]

['duncan', 'fluffy', 'jack', 'jake', 'jim']

In [8]:
import mysql.connector

#connecting to DB
cnx = mysql.connector.connect(user='push', password='ElI)g!LDOBIwM)%*5o5{dbfz('
                              ,host='127.0.0.1',database='edml')

In [9]:
cursor = cnx.cursor() #making a cursor to execute a SQL command
# cursor.execute("select * from post") #execute a command
cursor.execute("select * from post where user_id != (select user_id from user where user_login='recoverwithmeda')") #execute a command
myresult = cursor.fetchall() #get all the results 
print('{0} posts were retreived'.format(len(myresult))) 

8341 posts were retreived


In [10]:
#loading user_id and user_name to convert id to user_name
cursor.execute("select * from user") #execute a command
users = cursor.fetchall() #get all the results 
users = {i[0]:i[1] for i in users}
myresult = [i[0:2] + tuple([users[i[2]]]) + i[3:] for i in myresult]

#concatenating the old dataset to the new one
myresult_ = [tuple(i[1:]) for i in pd.read_csv('./data/old_ed.csv',index_col=None).values]
myresult += myresult_
print('{0} posts were retreived'.format(len(myresult))) 

21338 posts were retreived


In [21]:
# !pip install langdetect

In [11]:
from langdetect import detect
from tqdm import tqdm


# myresult = [s for s in myresult if len(remove_html_tags(s[3])) > 3 and detect(remove_html_tags(s[3]))=='en']
t = []
#removing tags and detecting language afterward
for s in tqdm(myresult):
    try:#in some case language detection may fail (emojies only, one word docs, etc.) ==> We don't keep those
        if detect(remove_html_tags(s[3]))=='en':
            t.append(s)
    except:
        pass #do nothing

myresult = t[:]
print('after removing non-english posts,the size of the documents are: {0}'.format(len(myresult)))

100%|██████████| 21338/21338 [02:07<00:00, 166.85it/s]

after removing non-english posts,the size of the documents are: 17306


In [12]:
#removing tags from texts
proc_texts = [remove_html_tags(i[3]) for i in myresult]
#pre_processing and tokenizing docs
pre_processed_docs,orig_docs = preprocess_data(proc_texts,extra_stopwords=stop_words)
#attaching (id,original_text,pre_processed_text,date,url) together
id_text = [(myresult[orig_docs[i][1]][0],orig_docs[i][0],pre_processed_docs[i],
            myresult[orig_docs[i][1]][4],myresult[orig_docs[i][1]][5],
            myresult[orig_docs[i][1]][2]) for i in range(len(orig_docs))]

# vocab_dict, doc_term_matrix = prepare_corpus(pre_processed_docs) ==> we don't need prepare corpus as we are passing this to LDA and STM R and there they will do tokenization 

#creat a pandas DF with one column as text, one column as original text, one column as SQL post-id, etc.
text_df = pd.DataFrame(zip([i[0] for i in id_text],[' '.join(i[2]) for i in id_text],
                           [i[1] for i in id_text],[i[3] for i in id_text],[i[4] for i in id_text],
                          [i[5] for i in id_text]),
                       columns=['id','text','original_text','date','url','blog'])


#removing duplicates only if necessary
print(len(text_df))
text_df = text_df.drop_duplicates(subset=['text'])
print(len(text_df))

14301
13590


In [13]:
wiki_path = './data/wiki_sampled_5p.txt'

In [14]:
import pickle

pre_processed_docs,_ = preprocess_data(list(text_df.text))
#preparing corpus
vocab_dict,doc_term_mat = prepare_corpus(pre_processed_docs)
#temp save of vocab file
vocab_path = "./data/ED_vocab.tmp"
with open (vocab_path,'wb') as vfile:
    pickle.dump(vocab_dict,vfile)

In [15]:
import pickle

wiki_vocab_path = './data/ref_corpus.vocab'
# with open(wiki_vocab_path,'wb') as f:
#     pickle.dump(wiki_vocab_dict,f)

In [33]:
# !pip install scikit-optimize

In [16]:
from skopt import BayesSearchCV
from skopt.space import Real, Categorical, Integer
from skopt.plots import plot_objective, plot_histogram
from lda_mallet import lda_score

params = dict()
params['num_topics'] = list(range(5,30,1))
params['alpha'] = list(range(25,100,25)) #Integer(65,100)
params['optimize_interval'] = list(range(100,300,100))
params['iterations'] = list(range(1000,5000,500))
params['wiki_path'] = [wiki_path] #this is a constant
params['db_path'] = ['./db/wiki_5p'] #this is a constant
params['vocab_dict_path'] = [vocab_path] #this is a constant
params['wiki_vocab_dict_path'] = [wiki_vocab_path] #this is a constant
params['npmi_skip_threshold'] = [0.33] #this is a single-value

# del pre_processed_docs, filtered_docs, vocab_dict#, doc_term_matrix
# del wiki_docs, wiki_vocab_dict, pre_processed_wiki

opt = BayesSearchCV(lda_score(),params,n_iter=10,n_jobs=10)

In [17]:
#fit the optimizer
opt.fit(doc_term_mat)

Mallet LDA: 7 topics, 3 topic bits, 111 topic mask
Data loaded.
Mallet LDA: 7 topics, 3 topic bits, 111 topic mask
max tokens: 832
total tokens: 384297
Mallet LDA: 7 topics, 3 topic bits, 111 topic mask
Mallet LDA: 7 topics, 3 topic bits, 111 topic mask
Data loaded.
Mallet LDA: 7 topics, 3 topic bits, 111 topic mask
max tokens: 832
total tokens: 467354
Data loaded.
Data loaded.
max tokens: 832
total tokens: 465809
Data loaded.
max tokens: 832
total tokens: 482401
max tokens: 684
total tokens: 493211
<10> LL/token: -9.19466
<10> LL/token: -8.88315
<10> LL/token: -8.88701
<20> LL/token: -8.7363
<10> LL/token: -8.90462
<10> LL/token: -8.95413
<30> LL/token: -8.48343
<20> LL/token: -8.44452
<20> LL/token: -8.40823
<20> LL/token: -8.45681
<20> LL/token: -8.4104
<40> LL/token: -8.36315
<30> LL/token: -8.27095
<30> LL/token: -8.2337
<30> LL/token: -8.28535
<30> LL/token: -8.24549

0	10.71429	eating recovery food disorder health ed support care mental disorders calories alliance proud binge ho

Load NPMI coherence DB. 
Number of keys : 27425
skipping 0 missed term-pairs < allowed misses = 0.33
Load NPMI coherence DB. 
Number of keys : 27425
skipping 0 missed term-pairs < allowed misses = 0.33


[nltk_data] Downloading package stopwords to /home/amh418/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /home/amh418/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package omw-1.4 to /home/amh418/nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /home/amh418/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
Mallet LDA: 12 topics, 4 topic bits, 1111 topic mask
Data loaded.
max tokens: 832
total tokens: 467354
Mallet LDA: 12 topics, 4 topic bits, 1111 topic mask
Data loaded.
max tokens: 832
total tokens: 384297
Mallet LDA: 12 topics, 4 topic bits, 1111 topic mask
Data loaded.
<10> LL/token: -9.05533
Mallet LDA: 12 topics, 4 topic bits, 1111 topic mask
Mallet LDA: 12 topics, 4 topic bits, 1111 topic mask
max tokens: 832
total tokens: 465

Load NPMI coherence DB. 
Number of keys : 27425
skipping 0 missed term-pairs < allowed misses = 0.33


<10> LL/token: -9.12354
[nltk_data] Downloading package stopwords to /home/amh418/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /home/amh418/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package omw-1.4 to /home/amh418/nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /home/amh418/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!


...

Load NPMI coherence DB. 
Number of keys : 27425
skipping 0 missed term-pairs < allowed misses = 0.33
Load NPMI coherence DB. 
Number of keys : 27425
skipping 0 missed term-pairs < allowed misses = 0.33
Load NPMI coherence DB. 
Number of keys : 27425
skipping 0 missed term-pairs < allowed misses = 0.33


[nltk_data] Downloading package stopwords to /home/amh418/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /home/amh418/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package omw-1.4 to /home/amh418/nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /home/amh418/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
<620> LL/token: -8.10247
<630> LL/token: -8.10928
<640> LL/token: -8.11211

0	1.7776	vegan cream favorite based free easy ice plant find perfect super simple fall fun water love protein full side delicious 
1	1.60995	body weight health healthy diet calories exercise gain workout lose fat important number culture physical lifestyle loss gym live working 
2	1.67288	guys video big amazing full bit week honestly holly pretty hair watch

Load NPMI coherence DB. 
Number of keys : 27425
skipping 0 missed term-pairs < allowed misses = 0.33
Load NPMI coherence DB. 
Number of keys : 27425
skipping 0 missed term-pairs < allowed misses = 0.33
Load NPMI coherence DB. 
Number of keys : 27425
skipping 0 missed term-pairs < allowed misses = 0.33



0	1.7776	vegan cream based easy favorite perfect ice plant free find super enjoy fall water love simple fun side fruit cut 
1	1.60995	body weight health healthy diet exercise gain lose physical workout fat number culture working lifestyle important loss gym mental matter 
2	1.67288	guys video week pretty big bit full amazing live holly day honestly coming happy vlog fun yesterday hair watch ps 
3	1.48718	hope post people comment find read share tree_html social book sharing reading content follow world posted instagram story picture amazing 
4	1.53886	body real skin happy photos things beautiful bodies wear image people monday positive beauty love online change comments comfortable human 
5	2.01147	day today days feeling work hard bad lot things great friends pretty rest put taking long back nice sad friend 
6	1.0392	#glutenfree #wellness #healthy #fitness #healthyfood #foodie #foodblogger #healthyinspo #thenewhealth #healthylife #cleaneats #plantpower #healthymeals #paleo #grainfree 

BayesSearchCV(estimator=<lda_mallet.lda_score object at 0x7f2dfa064580>,
              n_iter=10, n_jobs=10,
              search_spaces={'alpha': [25, 50, 75], 'db_path': ['./db/wiki_5p'],
                             'iterations': [1000, 1500, 2000, 2500, 3000, 3500,
                                            4000, 4500],
                             'npmi_skip_threshold': [0.33],
                             'num_topics': [5, 6, 7, 8, 9, 10, 11, 12, 13, 14,
                                            15, 16, 17, 18, 19, 20, 21, 22, 23,
                                            24, 25, 26, 27, 28, 29],
                             'optimize_interval': [100, 200],
                             'vocab_dict_path': ['./data/ED_vocab.tmp'],
                             'wiki_path': ['./data/wiki_sampled_5p.txt'],
                             'wiki_vocab_dict_path': ['./data/ref_corpus.vocab']})

In [19]:
print("val. score: %s" % opt.best_score_)
print("best params: %s" % str(opt.best_params_))

val. score: 0.12562945614064747
best params: OrderedDict([('alpha', 50), ('db_path', './db/wiki_5p'), ('iterations', 2000), ('npmi_skip_threshold', 0.33), ('num_topics', 19), ('optimize_interval', 200), ('vocab_dict_path', './data/ED_vocab.tmp'), ('wiki_path', './data/wiki_sampled_5p.txt'), ('wiki_vocab_dict_path', './data/ref_corpus.vocab')])


In [38]:
import matplotlib.pyplot as plt

_ = plot_objective(opt.optimizer_results_[0],
                   dimensions=["alpha", "iterations", "optimize_interval","num_topics"],
                   n_minimum_search=int(1e8))
plt.show()

IndexError: tuple index out of range

<Figure size 576x576 with 16 Axes>

In [21]:
opt.total_iterations

90